In [4]:
from flask import Flask, render_template, request, redirect, url_for, session
import random

app = Flask(__name__)
app.secret_key = 'your_secret_key'  # You must have a secret key for sessions to work

# Function to parse the questions from the file
def parse_questions(file_path, file_path2):
    with open(file_path, 'r', encoding='utf-8') as file:
        content = file.read().split("\n\n")  # Split content by empty lines between questions

    with open(file_path2, 'r', encoding='utf-8') as file:
        content = file.read().split("\n\n")  # Split content by empty lines between questions


    questions = []

    for block in content:
        lines = block.strip().split("\n")
        question = lines[0].replace("Kérdés: ", "").strip()  # Remove 'Kérdés:' from the start
        answers = []
        correct_answers = []

        # Parse the answers and separate correct answers (those starting with '!')
        for line in lines[1:]:
            answer = line.strip()
            if answer.startswith('!'):
                correct_answers.append(answer[1:].strip())  # Remove the '!' and save the correct answer
            else:
                answers.append(answer)

        # Add the parsed question, answers, and correct answers to the list
        if correct_answers:
            questions.append({
                'question': question,
                'answers': answers + correct_answers,  # Append correct answers at the end
                'correct_answers': correct_answers
            })

    return questions

# Parse questions from the file
questions = parse_questions('kerdessor1.txt', 'kerdessor2.txt')

@app.route('/')
def index():
    # Initialize the quiz session
    if 'selected_questions' not in session:
        selected_questions = random.sample(questions, 10)
        session['selected_questions'] = selected_questions
        session['question_index'] = 0
        session['answers'] = []  # Clear answers to start fresh

    else:
        selected_questions = session['selected_questions']

    question_index = session.get('question_index', 0)

    # If all questions are answered, redirect to the results page
    if question_index >= len(selected_questions):
        return redirect(url_for('result'))

    # Get the current question
    current_question = selected_questions[question_index]

    # Shuffle the answers to randomize their order
    random.shuffle(current_question['answers'])

    return render_template('quiz.html', question=current_question, question_index=question_index)

@app.route('/submit_answer', methods=['POST'])
def submit_answer():
    # Get the user's answer and the current question index
    user_answers = request.form.getlist('answer')  # Use getlist for checkboxes (multiple answers)
    question_index = int(request.form.get('question_index'))
    
    # Store the answer in the session
    answers = session.get('answers', [])
    answers.append(user_answers)
    session['answers'] = answers

    # Move to the next question
    question_index += 1
    session['question_index'] = question_index
    
    return redirect(url_for('index'))


@app.route('/result')
def result():
    # Ensure 'selected_questions' exists in the session
    selected_questions = session.get('selected_questions', None)
    answers = session.get('answers', None)

    if not selected_questions or not answers:
        return redirect(url_for('index'))  # Redirect back to the quiz if selected_questions or answers are missing

    # Calculate the score and track mistakes
    score = 0
    mistakes = []

    for i, user_answer in enumerate(answers):
        correct_answers = selected_questions[i]['correct_answers']
        
        # Check if the selected answers exactly match the correct answers (order doesn't matter)
        if set(user_answer) == set(correct_answers):
            score += 1
        else:
            mistakes.append({
                'question': selected_questions[i]['question'],
                'correct_answer': correct_answers,
                'user_answer': user_answer
            })

    # Prepare zipped data to pass to the template (question, user answer pair)
    questions_with_answers = zip(selected_questions, answers)

    # Reset session data so the user can restart the quiz or continue
    session.pop('question_index', None)  # Clear the current question index
    session.pop('answers', None)  # Clear stored answers
    session.pop('selected_questions', None)  # Clear selected questions

    return render_template('result.html', score=score, total=len(selected_questions), mistakes=mistakes, questions_with_answers=questions_with_answers)


@app.route('/restart')
def restart():
    # Clear session data to restart the quiz
    session.pop('question_index', None)
    session.pop('answers', None)
    session.pop('selected_questions', None)
    
    return redirect(url_for('index'))  # Redirect to start the quiz again

if __name__ == '__main__':
    app.run()


 * Serving Flask app '__main__'
 * Debug mode: off


 * Running on http://127.0.0.1:5000
Press CTRL+C to quit
127.0.0.1 - - [07/Jan/2025 08:55:19] "GET / HTTP/1.1" 200 -
127.0.0.1 - - [07/Jan/2025 08:55:30] "POST /submit_answer HTTP/1.1" 302 -
127.0.0.1 - - [07/Jan/2025 08:55:30] "GET / HTTP/1.1" 200 -
127.0.0.1 - - [07/Jan/2025 08:55:40] "POST /submit_answer HTTP/1.1" 302 -
127.0.0.1 - - [07/Jan/2025 08:55:40] "GET / HTTP/1.1" 200 -
127.0.0.1 - - [07/Jan/2025 08:55:59] "POST /submit_answer HTTP/1.1" 302 -
127.0.0.1 - - [07/Jan/2025 08:55:59] "GET / HTTP/1.1" 200 -
127.0.0.1 - - [07/Jan/2025 08:56:09] "POST /submit_answer HTTP/1.1" 302 -
127.0.0.1 - - [07/Jan/2025 08:56:09] "GET / HTTP/1.1" 200 -
127.0.0.1 - - [07/Jan/2025 08:56:17] "POST /submit_answer HTTP/1.1" 302 -
127.0.0.1 - - [07/Jan/2025 08:56:17] "GET / HTTP/1.1" 200 -
127.0.0.1 - - [07/Jan/2025 08:56:21] "POST /submit_answer HTTP/1.1" 302 -
127.0.0.1 - - [07/Jan/2025 08:56:21] "GET / HTTP/1.1" 200 -
127.0.0.1 - - [07/Jan/2025 08:56:50] "POST /submit_answer HTTP/1.1" 302 -
127.0